#### Importing Libraries


In [156]:


import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print("Libraries imported.")


Libraries imported.


#### Data Scrapping from wikipedia page into a DataFrame

In [68]:
# send the GET request
data = requests.get("https://en.wikipedia.org/wiki/List_of_suburbs_of_Auckland").text

In [69]:
# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(data, 'html.parser')

In [70]:
# create a list to store neighborhood data
neighborhoodList = []

In [71]:
# append the data into the list
for row in soup.find_all("div", class_="mw-parser-output")[0].findAll("li"):
    neighborhoodList.append(row.text)

##### Creating and Cleaning Data

In [113]:

# create a new DataFrame from the list
kl_df = pd.DataFrame({"Neighborhood": neighborhoodList})
auc_df=kl_df.iloc[8:].reset_index(drop=True)
auc_df

Neighborhood
0                                            Arch Hill
1                                         Auckland CBD
2                                             Avondale
3                                             Balmoral
4                                            Blackpool
5                                       Blockhouse Bay
6                                         Eden Terrace
7                                          Eden Valley
8                                            Ellerslie
9                                                Epsom
10                                        Freemans Bay
11                                           Glendowie
12                                          Glen Innes
13                                             Grafton
14                                           Greenlane
15                                   Greenwoods Corner
16                                           Grey Lynn
17                                           Herne Bay
18                                        Hillsborough
19                                           Kingsland
20                                          Kohimarama
21                                            Lynfield
22                                          Meadowbank
23                                         Mission Bay
24                                         Morningside
25                                        Mount Albert
26                                          Mount Eden
27                                       Mount Roskill
28                                    Mount Wellington
29                                           Newmarket
30                                              Newton
31                                         New Windsor
32                                            Onehunga
33                                              Oneroa
34                                            Onetangi
35                                       One Tree Hill
36                                              Orakei
37                                              Oranga
38                                              Ostend
39                                             Otahuhu
40                                            Owairaka
41                                          Palm Beach
42                                             Panmure
43                                             Parnell
44                                             Penrose
45                                       Point England
46                                     Point Chevalier
47                                            Ponsonby
48                                             Remuera
49                                           Royal Oak
50                                       Saint Heliers
51                                         Saint Johns
52                                     Saint Marys Bay
53                                         Sandringham
54                                         Stonefields
55                                              Tamaki
56                                           Te Papapa
57                                         Three Kings
58                                           Waikowhai
59                                     Wai o Taiki Bay
60                                           Waterview
61                                     Western Springs
62                                           Westfield
63                                            Westmere
64                                              Albany
65                                           Bayswater
66                                             Bayview
67                                         Beach Haven
68                                             Belmont
69                                            Birkdale
70                                          Birkenhead
71                                          Browns Bay
72                         

In [114]:
# print the number of rows of the dataframe
auc_df.shape

(304, 1)

#### Getting geographical co-ordinates

In [115]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Auckland, New Zealand'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [116]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in auc_df["Neighborhood"].tolist() ]

In [117]:
coords

[[-36.86301999999995, 174.74858000000006],
 [-36.84839904099994, 174.76438785300002],
 [-36.89044821899995, 174.6870174820001],
 [-36.88819999999998, 174.7401900000001],
 [-37.05156381518735, 174.8843945401761],
 [-36.92819999999995, 174.70019000000002],
 [-36.86413508299995, 174.75743271800002],
 [-36.96750084635119, 174.83853712187494],
 [-36.896377420999954, 174.81373710200012],
 [-36.88845407399998, 174.77293816600002],
 [-36.85287929799995, 174.75035326400007],
 [-36.86036095299994, 174.87265930000012],
 [-36.87394120099998, 174.86095625600012],
 [-36.85329999999993, 174.77975000000004],
 [-36.89491322499998, 174.79262520600003],
 [-36.92865406512159, 174.64980256580628],
 [-36.861568621999936, 174.73955514300008],
 [-36.83819999999997, 174.72019000000012],
 [-36.92389779599995, 174.75536291900005],
 [-36.87019698199998, 174.7452094570001],
 [-36.85725985999994, 174.84097833500005],
 [-36.93035918099997, 174.71985815800008],
 [-36.86950058399998, 174.82957281000006],
 [-38.8982299

In [118]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [119]:
# merge the coordinates into the original dataframe
auc_df['Latitude'] = df_coords['Latitude']
auc_df['Longitude'] = df_coords['Longitude']

In [120]:
# check the neighborhoods and the coordinates
print(auc_df.shape)
auc_df

(304, 3)


Neighborhood   Latitude   Longitude
0                                            Arch Hill -36.863020  174.748580
1                                         Auckland CBD -36.848399  174.764388
2                                             Avondale -36.890448  174.687017
3                                             Balmoral -36.888200  174.740190
4                                            Blackpool -37.051564  174.884395
5                                       Blockhouse Bay -36.928200  174.700190
6                                         Eden Terrace -36.864135  174.757433
7                                          Eden Valley -36.967501  174.838537
8                                            Ellerslie -36.896377  174.813737
9                                                Epsom -36.888454  174.772938
10                                        Freemans Bay -36.852879  174.750353
11                                           Glendowie -36.860361  174.872659
12                                          Glen Innes -36.873941  174.860956
13                                             Grafton -36.853300  174.779750
14                                           Greenlane -36.894913  174.792625
15                                   Greenwoods Corner -36.928654  174.649803
16                                           Grey Lynn -36.861569  174.739555
17                                           Herne Bay -36.838200  174.720190
18                                        Hillsborough -36.923898  174.755363
19                                           Kingsland -36.870197  174.745209
20                                          Kohimarama -36.857260  174.840978
21                                            Lynfield -36.930359  174.719858
22                                          Meadowbank -36.869501  174.829573
23                                         Mission Bay -38.898230  175.930210
24                                         Morningside -36.868200  174.730190
25                                        Mount Albert -36.884724  174.717695
26                                          Mount Eden -36.883602  174.754237
27                                       Mount Roskill -36.916066  174.736536
28                                    Mount Wellington -36.912733  174.839904
29                                           Newmarket -36.867410  174.776385
30                                              Newton -36.850000  174.750000
31                                         New Windsor -36.905310  174.712787
32                                            Onehunga -36.920599  174.790655
33                                              Oneroa -36.778190  175.010190
34                                            Onetangi -36.783330  175.083330
35                                       One Tree Hill -36.904613  174.789187
36                                              Orakei -36.850000  174.816670
37                                              Oranga -36.908200  174.790190
38                                              Ostend -36.798200  175.040190
39                                             Otahuhu -36.943905  174.845226
40                                            Owairaka -36.888200  174.710190
41                                          Palm Beach -36.913905  174.869455
42                                             Panmure -36.897420  174.859564
43                                             Parnell -36.854070  174.779340
44                                             Penrose -36.918134  174.817623
45                                       Point England -36.883958  174.864695
46                                     Point Chevalier -36.866297  174.706425
47                                            Ponsonby -36.850733  174.739223
48                                             Remuera -36.877404  174.805492
49                                           Royal Oak -36.910653  174.772330
50                                       Saint Heliers -36.85000

In [121]:
# save the DataFrame as CSV file
auc_df.to_csv("auck_df.csv", index= False)

#### Creating a Map of Auckland with superimposed neighbors on top

In [122]:
# get the coordinates of Kuala Lumpur
address = 'Auckland , New Zealand'

geolocator = Nominatim(user_agent="auc-data")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Auckland, NewZealand {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Auckland, NewZealand -36.852095, 174.7631803.


In [123]:
# create map of Auckland using latitude and longitude values
map_auc = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(auc_df['Latitude'], auc_df['Longitude'], auc_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_auc)  
    
map_auc

In [124]:
# save the map as HTML file
map_auc.save('map_auck.html')

#### Using Foursquare API to explore the neighborhoods

In [157]:
# define Foursquare Credentials and Version
CLIENT_ID = 'CLIENT_ID' # your Foursquare ID
CLIENT_SECRET = 'CLIENT_SECRET' # your Foursquare Secret
VERSION = '20200817' # Foursquare API version

print('Your credentail input complete:')


Your credentail input complete:


In [ ]:
radius = 1000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(auc_df['Latitude'], auc_df['Longitude'], auc_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [162]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(4773, 7)


Neighborhood  Latitude  Longitude       VenueName  VenueLatitude  \
0    Arch Hill -36.86302  174.74858  Grey Lynn Park     -36.861524   
1    Arch Hill -36.86302  174.74858    Charlie Boys     -36.862712   
2    Arch Hill -36.86302  174.74858       Countdown     -36.858375   
3    Arch Hill -36.86302  174.74858           Azabu     -36.859196   
4    Arch Hill -36.86302  174.74858     eighthirty™     -36.859233   

   VenueLongitude        VenueCategory  
0      174.743148                 Park  
1      174.748618                 Café  
2      174.748862               Market  
3      174.751613  Japanese Restaurant  
4      174.753297                 Café

In [131]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                         
Airport Oaks                5          5          5              5   
Albany                     30         30         30             30   
Alfriston                   1          1          1              1   
Algies Bay                 89         89         89             89   
Ararimu                    89         89         89             89   
Arch Hill                  77         77         77             77   
Ardmore                    72         72         72             72   
Arkles Bay                  4          4          4              4   
Army Bay                    2          2          2              2   
Auckland CBD               89         89         89             89   
Avondale                    9          9          9              9   
Awhitu                     89         89         89             89   
Balmoral                   69         69         69             69   
Bayswater                   4          4          4              4   
Bayview                     5          5          5              5   
Beach Haven                12         12         12             12   
Belmont                    14         14         14             14   
Birkdale                    7          7          7              7   
Birkenhead                 25         25         25             25   
Blackpool                   4          4          4              4   
Blockhouse Bay              7          7          7              7   
Bombay                     89         89         89             89   
Botany Downs                8          8          8              8   
Browns Bay                 14         14         14             14   
Buckland                    6          6          6              6   
Bucklands Beach             4          4          4              4   
Burswood                   14         14         14             14   
Campbells Bay               4          4          4              4   
Castor Bay                  8          8          8              8   
Chapel Downs               21         21         21             21   
Chatswood                  13         13         13             13   
Cheltenham                 19         19         19             19   
Clarks Beach                6          6          6              6   
Clendon Park                4          4          4              4   
Clevedon                   89         89         89             89   
Clover Park                 8          8          8              8   
Cockle Bay                  4          4          4              4   
Conifer Grove               6          6          6              6   
Cornwallis                  2          2          2              2   
Crown Hill                  8          8          8              8   
Dannemora                  15         15         15             15   
Devonport                  38         38         38             38   
Drury                      41         41         41             41   
East Tamaki                 6          6          6              6   
East Tamaki Heights         2          2          2              2   
Eastern Beach               4          4          4              4   
Eden Terrace              100        100        100            100   
Eden Valley                 6          6          6              6   
Ellerslie                  32         32         32             32   
Epsom                      22         22         22             22   
Fairview Heights            6          6          6              6   
Farm Cove                   5          5          5              5   
Favona                      6          6          6              6   
Flamboro Heights           89         89         89             89   
Flat Bush                   3          3          3              3   
Forrest Hill               41  

##### Finding Unique columns

In [132]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 263 uniques categories.


In [133]:
# print out the list of categories
venues_df['VenueCategory'].unique()[:50]

array(['Park', 'Café', 'Market', 'Japanese Restaurant', 'Dance Studio',
       'Gym / Fitness Center', 'Food Court', 'Argentinian Restaurant',
       'Shopping Mall', 'South Indian Restaurant', 'Pizza Place',
       'Burger Joint', 'Hostel', 'Toy / Game Store',
       'Fruit & Vegetable Store', 'Bistro', 'Bakery',
       'Italian Restaurant', 'Restaurant', 'Mexican Restaurant',
       'Thai Restaurant', 'General Entertainment',
       'Vietnamese Restaurant', 'Bar', 'Malay Restaurant',
       'American Restaurant', 'Ice Cream Shop', 'Music Venue',
       'Asian Restaurant', 'New American Restaurant', 'Gym',
       'Thrift / Vintage Store', 'Sporting Goods Shop',
       'African Restaurant', 'Grocery Store', 'Lebanese Restaurant',
       'Sandwich Place', 'Speakeasy', 'Pharmacy', 'Skate Park',
       'Food & Drink Shop', 'Chinese Restaurant', 'Fast Food Restaurant',
       'Athletics & Sports', 'Sushi Restaurant', 'Deli / Bodega',
       'Monument / Landmark', 'Steakhouse', 'Tapas Resta

In [134]:
# check if the results contain "Shopping Mall"
"Neighborhood" in venues_df['VenueCategory'].unique()

True

#### Analyzing each Neighborhood

In [136]:
# one hot encoding
auc_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
auc_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [auc_onehot.columns[-1]] + list(auc_onehot.columns[:-1])
auc_onehot = auc_onehot[fixed_columns]

print(auc_onehot.shape)
auc_onehot.head()

(5017, 264)


Neighborhoods  African Restaurant  Airport  American Restaurant  \
0     Arch Hill                   0        0                    0   
1     Arch Hill                   0        0                    0   
2     Arch Hill                   0        0                    0   
3     Arch Hill                   0        0                    0   
4     Arch Hill                   0        0                    0   

   Antique Shop  Aquarium  Arcade  Argentinian Restaurant  Art Gallery  \
0             0         0       0                       0            0   
1             0         0       0                       0            0   
2             0         0       0                       0            0   
3             0         0       0                       0            0   
4             0         0       0                       0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0                    0                 0                   0   
1                    0                 0                   0   
2                    0                 0                   0   
3                    0                 0                   0   
4                    0                 0                   0   

   Australian Restaurant  Automotive Shop  BBQ Joint  Badminton Court  \
0                      0                0          0                0   
1                      0                0          0                0   
2                      0                0          0                0   
3                      0                0          0                0   
4                      0                0          0                0   

   Bagel Shop  Bakery  Bar  Baseball Field  Basketball Court  \
0           0       0    0               0                 0   
1           0       0    0               0                 0   
2           0       0    0               0                 0   
3           0       0    0               0                 0   
4           0       0    0               0                 0   

   Basketball Stadium  Beach  Beer Bar  Beer Garden  Big Box Store  \
0                   0      0         0            0              0   
1                   0      0         0            0              0   
2                   0      0         0            0              0   
3                   0      0         0            0              0   
4                   0      0         0            0              0   

   Bike Trail  Bistro  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0           0       0              0          0                 0         0   
1           0       0              0          0                 0         0   
2           0       0              0          0                 0         0   
3           0       0              0          0                 0         0   
4           0       0              0          0                 0         0   

   Bowling Alley  Bowling Green  Brazilian Restaurant  Breakfast Spot  \
0              0              0                     0               0   
1              0              0                     0               0   
2              0              0                     0               0   
3              0              0                     0               0   
4              0              0                     0               0   

   Brewery  Bubble Tea Shop  Buffet  Burger Joint  Bus Station  Bus Stop  \
0        0                0       0             0            0         0   
1        0                0       0             0            0         0   
2        0                0       0             0            0         0   
3        0                0       0             0            0         0   
4        0                0       0             0            0         0   

   Business Service  Cafeteria  Café  Cajun / Creole Restaurant  Campground  \
0                 0          0     0                          

In [137]:
auc_grouped = auc_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(auc_grouped.shape)
auc_grouped

(232, 264)


Neighborhoods  African Restaurant   Airport  American Restaurant  \
0           Airport Oaks            0.000000  0.000000             0.000000   
1                 Albany            0.000000  0.000000             0.000000   
2              Alfriston            0.000000  0.000000             0.000000   
3             Algies Bay            0.000000  0.000000             0.000000   
4                Ararimu            0.000000  0.000000             0.000000   
5              Arch Hill            0.012987  0.000000             0.012987   
6                Ardmore            0.000000  0.000000             0.013889   
7             Arkles Bay            0.000000  0.000000             0.000000   
8               Army Bay            0.000000  0.000000             0.000000   
9           Auckland CBD            0.000000  0.000000             0.000000   
10              Avondale            0.000000  0.000000             0.000000   
11                Awhitu            0.000000  0.000000             0.000000   
12              Balmoral            0.000000  0.000000             0.000000   
13             Bayswater            0.000000  0.000000             0.000000   
14               Bayview            0.000000  0.000000             0.000000   
15           Beach Haven            0.000000  0.000000             0.000000   
16               Belmont            0.000000  0.000000             0.000000   
17              Birkdale            0.000000  0.000000             0.000000   
18            Birkenhead            0.000000  0.000000             0.000000   
19             Blackpool            0.000000  0.000000             0.000000   
20        Blockhouse Bay            0.000000  0.000000             0.000000   
21                Bombay            0.000000  0.000000             0.000000   
22          Botany Downs            0.000000  0.000000             0.000000   
23            Browns Bay            0.000000  0.000000             0.000000   
24              Buckland            0.000000  0.000000             0.000000   
25       Bucklands Beach            0.000000  0.000000             0.000000   
26              Burswood            0.000000  0.000000             0.000000   
27         Campbells Bay            0.000000  0.000000             0.000000   
28            Castor Bay            0.000000  0.000000             0.000000   
29          Chapel Downs            0.000000  0.000000             0.000000   
30             Chatswood            0.000000  0.000000             0.000000   
31            Cheltenham            0.000000  0.000000             0.000000   
32          Clarks Beach            0.000000  0.000000             0.000000   
33          Clendon Park            0.000000  0.000000             0.000000   
34              Clevedon            0.000000  0.000000             0.000000   
35           Clover Park            0.000000  0.000000             0.000000   
36            Cockle Bay            0.000000  0.000000             0.000000   
37         Conifer Grove            0.000000  0.000000             0.000000   
38            Cornwallis            0.000000  0.000000             0.000000   
39            Crown Hill            0.000000  0.000000             0.000000   
40             Dannemora            0.000000  0.000000             0.000000   
41             Devonport            0.000000  0.000000             0.000000   
42                 Drury            0.000000  0.000000             0.024390   
43           East Tamaki            0.000000  0.000000             0.000000   
44   East Tamaki Heights            0.000000  0.000000             0.000000   
45         Eastern Beach            0.000000  0.000000             0.000000   
46          Eden Terrace            0.010000  0.000000             0.010000   
47           Eden Valley            0.000000  0.000000             0.000000   
48             Ellerslie            0.000000  0.000000             0.000000   
49                 Epsom            0.000000  0.000000       

In [138]:
len(auc_grouped[auc_grouped["Shopping Mall"] > 0])

48

In [139]:
auc_mall = auc_grouped[["Neighborhoods","Shopping Mall"]]

In [140]:
auc_mall.head()

Neighborhoods  Shopping Mall
0  Airport Oaks       0.000000
1        Albany       0.033333
2     Alfriston       0.000000
3    Algies Bay       0.000000
4       Ararimu       0.000000

#### Clustering Neighborhoods
Here we are using K-means Algorithm

In [141]:
# set number of clusters
kclusters = 3

auc_clustering = auc_mall.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(auc_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [142]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
auc_merged = auc_mall.copy()

# add clustering labels
auc_merged["Cluster Labels"] = kmeans.labels_

In [144]:
auc_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
auc_merged.head(10)

Neighborhood  Shopping Mall  Cluster Labels
0  Airport Oaks       0.000000               0
1        Albany       0.033333               0
2     Alfriston       0.000000               0
3    Algies Bay       0.000000               0
4       Ararimu       0.000000               0
5     Arch Hill       0.012987               0
6       Ardmore       0.013889               0
7    Arkles Bay       0.000000               0
8      Army Bay       0.000000               0
9  Auckland CBD       0.000000               0

In [149]:
# merge Auckland_grouped with Auckland_data to add latitude/longitude for each neighborhood
auc_merged = auc_merged.join(kl_df.set_index("Neighborhood"), on="Neighborhood")

print(auc_merged.shape)
auc_merged.head() # check the last columns!

(232, 5)


Neighborhood  Shopping Mall  Cluster Labels   Latitude   Longitude
0  Airport Oaks       0.000000               0 -36.793590  174.618012
1        Albany       0.033333               0 -36.734272  174.699281
2     Alfriston       0.000000               0 -37.010493  174.940852
3    Algies Bay       0.000000               0 -36.848399  174.764388
4       Ararimu       0.000000               0 -36.848399  174.764388

In [150]:
# sort the results by Cluster Labels
print(auc_merged.shape)
auc_merged.sort_values(["Cluster Labels"], inplace=True)
auc_merged

(232, 5)


Neighborhood  Shopping Mall  Cluster Labels   Latitude   Longitude
0           Airport Oaks       0.000000               0 -36.793590  174.618012
142               Orakei       0.000000               0 -36.850000  174.816670
143               Oranga       0.000000               0 -36.908200  174.790190
144               Oratia       0.000000               0 -36.927315  174.611793
145             Ormiston       0.000000               0 -36.961831  174.891565
146               Ostend       0.000000               0 -36.798200  175.040190
147              Otahuhu       0.000000               0 -36.943905  174.845226
149                Oteha       0.000000               0 -36.719683  174.719236
150             Owairaka       0.000000               0 -36.888200  174.710190
151              Paerata       0.000000               0 -36.887045  174.859215
152           Pahurehure       0.000000               0 -37.058200  174.920190
154    Pakuranga Heights       0.000000               0 -36.912258  174.893306
156              Panmure       0.000000               0 -36.897420  174.859564
157             Paparimu       0.000000               0 -36.848399  174.764388
158           Papatoetoe       0.000000               0 -36.976920  174.855379
159                Parau       0.000000               0 -36.966670  174.616670
160           Paremoremo       0.000000               0 -36.766670  174.666670
161              Parnell       0.011111               0 -36.854070  174.779340
162            Patumahoe       0.000000               0 -36.848399  174.764388
164             Pinehill       0.000000               0 -36.731441  174.723566
165      Point Chevalier       0.000000               0 -36.866297  174.706425
166        Point England       0.000000               0 -36.883958  174.864695
167               Pollok       0.000000               0 -36.848399  174.764388
168             Ponsonby       0.024691               0 -36.850733  174.739223
141             Onetangi       0.000000               0 -36.783330  175.083330
169        Randwick Park       0.000000               0 -37.023824  174.918056
140               Oneroa       0.000000               0 -36.778190  175.010190
137                Okura       0.000000               0 -36.679063  174.724200
111             Maraetai       0.000000               0 -36.887735  175.038039
113               Massey       0.000000               0 -36.838736  174.600847
114         McLaren Park       0.000000               0 -36.888200  174.610190
230         Windsor Park       0.000000               0 -36.743140  174.737270
116          Meadowlands       0.000000               0 -36.908781  174.941211
117          Mellons Bay       0.000000               0 -36.878200  174.920190
118           Middlemore       0.000000               0 -36.966209  174.844730
120          Morningside       0.000000               0 -36.868200  174.730190
121         Mount Albert       0.000000               0 -36.884724  174.717695
122           Mount Eden       0.000000               0 -36.883602  174.754237
123        Mount Roskill       0.000000               0 -36.916066  174.736536
124     Mount Wellington       0.027027               0 -36.912733  174.839904
125      Murphys Heights       0.000000               0 -36.989480  174.915520
127          Narrow Neck       0.000000               0 -36.815421  174.799342
128             New Lynn       0.033333               0 -36.913037  174.678813
129          New Windsor       0.000000               0 -36.905310  174.712787
130            Newmarket       0.012048               0 -36.867410  174.776385
131               Newton       0.021739               0 -36.850000  174.750000
132        North Harbour       0.000000               0 -36.773910  174.738910
133           North Park       0.000000               0 -36.920491  174.919753
134            Northcote       0.000000               0 -36.803181  174.747020
135      Northcote Point       0.000000               0 -36.81

#### Finally Visualizing the Resulting Clusters

In [151]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(auc_merged['Latitude'], auc_merged['Longitude'], auc_merged['Neighborhood'], auc_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [152]:
# save the map as HTML file
map_clusters.save('map_cluster.html')

#### Examining Clusters

##### Cluster 0:

In [153]:
auc_merged.loc[auc_merged['Cluster Labels'] == 0]

Neighborhood  Shopping Mall  Cluster Labels   Latitude   Longitude
0           Airport Oaks       0.000000               0 -36.793590  174.618012
142               Orakei       0.000000               0 -36.850000  174.816670
143               Oranga       0.000000               0 -36.908200  174.790190
144               Oratia       0.000000               0 -36.927315  174.611793
145             Ormiston       0.000000               0 -36.961831  174.891565
146               Ostend       0.000000               0 -36.798200  175.040190
147              Otahuhu       0.000000               0 -36.943905  174.845226
149                Oteha       0.000000               0 -36.719683  174.719236
150             Owairaka       0.000000               0 -36.888200  174.710190
151              Paerata       0.000000               0 -36.887045  174.859215
152           Pahurehure       0.000000               0 -37.058200  174.920190
154    Pakuranga Heights       0.000000               0 -36.912258  174.893306
156              Panmure       0.000000               0 -36.897420  174.859564
157             Paparimu       0.000000               0 -36.848399  174.764388
158           Papatoetoe       0.000000               0 -36.976920  174.855379
159                Parau       0.000000               0 -36.966670  174.616670
160           Paremoremo       0.000000               0 -36.766670  174.666670
161              Parnell       0.011111               0 -36.854070  174.779340
162            Patumahoe       0.000000               0 -36.848399  174.764388
164             Pinehill       0.000000               0 -36.731441  174.723566
165      Point Chevalier       0.000000               0 -36.866297  174.706425
166        Point England       0.000000               0 -36.883958  174.864695
167               Pollok       0.000000               0 -36.848399  174.764388
168             Ponsonby       0.024691               0 -36.850733  174.739223
141             Onetangi       0.000000               0 -36.783330  175.083330
169        Randwick Park       0.000000               0 -37.023824  174.918056
140               Oneroa       0.000000               0 -36.778190  175.010190
137                Okura       0.000000               0 -36.679063  174.724200
111             Maraetai       0.000000               0 -36.887735  175.038039
113               Massey       0.000000               0 -36.838736  174.600847
114         McLaren Park       0.000000               0 -36.888200  174.610190
230         Windsor Park       0.000000               0 -36.743140  174.737270
116          Meadowlands       0.000000               0 -36.908781  174.941211
117          Mellons Bay       0.000000               0 -36.878200  174.920190
118           Middlemore       0.000000               0 -36.966209  174.844730
120          Morningside       0.000000               0 -36.868200  174.730190
121         Mount Albert       0.000000               0 -36.884724  174.717695
122           Mount Eden       0.000000               0 -36.883602  174.754237
123        Mount Roskill       0.000000               0 -36.916066  174.736536
124     Mount Wellington       0.027027               0 -36.912733  174.839904
125      Murphys Heights       0.000000               0 -36.989480  174.915520
127          Narrow Neck       0.000000               0 -36.815421  174.799342
128             New Lynn       0.033333               0 -36.913037  174.678813
129          New Windsor       0.000000               0 -36.905310  174.712787
130            Newmarket       0.012048               0 -36.867410  174.776385
131               Newton       0.021739               0 -36.850000  174.750000
132        North Harbour       0.000000               0 -36.773910  174.738910
133           North Park       0.000000               0 -36.920491  174.919753
134            Northcote       0.000000               0 -36.803181  174.747020
135      Northcote Point       0.000000               0 -36.81

##### Cluster 1:

In [154]:
auc_merged.loc[auc_merged['Cluster Labels'] == 1]

Neighborhood  Shopping Mall  Cluster Labels   Latitude   Longitude
148         Otara       0.333333               1 -36.962170  174.874850
219   Wattle Cove       0.250000               1 -36.893993  174.638942
221  West Harbour       0.166667               1 -36.815774  174.631958
201     Te Papapa       0.200000               1 -36.918200  174.800190
59       Glendene       0.250000               1 -36.890409  174.654240

##### Cluster 2:

In [155]:
auc_merged.loc[auc_merged['Cluster Labels'] == 2]

Neighborhood  Shopping Mall  Cluster Labels   Latitude   Longitude
100       Lynfield       0.125000               2 -36.930359  174.719858
110  Manurewa East       0.083333               2 -37.025213  174.906037
102   Mairangi Bay       0.052632               2 -36.741048  174.747546
119        Milford       0.066667               2 -36.773338  174.760711
112    Marlborough       0.071429               2 -36.778200  174.720190
163        Penrose       0.083333               2 -36.918134  174.817623
213       Waiau Pa       0.090909               2 -36.693917  174.754361
126    Murrays Bay       0.058824               2 -36.731652  174.746350
205         Torbay       0.100000               2 -36.698190  174.750190
22    Botany Downs       0.125000               2 -36.909453  174.917068
29    Chapel Downs       0.047619               2 -36.938285  174.913718
139       Onehunga       0.047619               2 -36.920599  174.790655
78   Highland Park       0.071429               2 -36.904535  174.908448
72       Henderson       0.062500               2 -36.879786  174.622935
153      Pakuranga       0.076923               2 -36.914538  174.872924
176      Royal Oak       0.064516               2 -36.910653  174.772330
155     Palm Beach       0.076923               2 -36.913905  174.869455
61       Glenfield       0.058824               2 -36.782597  174.721587
214      Waikowhai       0.100000               2 -36.928200  174.730190
115     Meadowbank       0.043478               2 -36.869501  174.829573

### Final Observations:

##### 
Here we can see Most of the shopping malls are concentrated in the central-mid area of Auckland city, with the highest number in cluster 2 and moderate number in cluster 0. On the other hand, cluster 1 has very low number to totally no shopping mall in the neighborhoods. This represents a great opportunity and high potential areas to open new shopping malls as there is very little to no competition from existing malls. Meanwhile, shopping malls in cluster 2 are likely suffering from intense competition due to oversupply and high concentration of shopping malls. From another perspective, this also shows that the oversupply of shopping malls mostly happened in the central-mid area of the city, with the suburb area still have very few shopping malls. Therefore, this project recommends property developers to capitalize on these findings to open new shopping malls in neighborhoods in cluster 1 with little to no competition. Property developers with unique selling propositions to stand out from the competition can also open new shopping malls in neighborhoods in cluster 0 with moderate competition. Lastly, property developers are advised to avoid neighborhoods in cluster 2 which already have high concentration of shopping malls and suffering from intense competition.